In [3]:
import logging

from absl import app
from absl import flags
import apache_beam as beam
import xarray as xr
import xarray_beam as xbeam
import xee

import ee
import geemap

import pyproj

import os
import xarray as xr
import geopandas as gp
import pandas as pd
import numpy as np
import sparse

import hvplot.pandas
import hvplot.xarray
import dask
import cf_xarray

from pynhd import NLDI, WaterData
import intake
import cartopy.crs as ccrs
from shapely.geometry import Polygon

import time
import dask
import requests
from dask.distributed import Client

import requests
from IPython.display import HTML
import warnings
from IPython.display import HTML

from pynhd import NLDI, WaterData
import matplotlib.pyplot as plt
import geopandas as gpd
import contextily as ctx


In [6]:
# Step 1: Authenticate Earth Engine
ee.Authenticate()

True

In [9]:
geemap.ee_initialize()
ee.Initialize(project="ee-mikediastat")

### CONUS404

In [12]:
# open the hytest data intake catalog
hytest_cat = intake.open_catalog("https://raw.githubusercontent.com/hytest-org/hytest/main/dataset_catalog/hytest_intake_catalog.yml")
list(hytest_cat)

# open the conus404 sub-catalog
# cat = hytest_cat['conus404-catalog']
cat = hytest_cat['conus404-catalog']
list(cat)

## Select the dataset you want to read into your notebook and preview its metadata
#  conus404-daily-osn
dataset = 'conus404-daily-osn' 
cat[dataset]

print(f"Reading {dataset} metadata...", end='')
ds = cat[dataset].to_dask().metpy.parse_cf()
print("done")
ds
# ds_conus = ds.ACRAINLSM.sel(time=slice('2010-01-01','2020-12-31')).load()
ds_conus = ds.sel(time=slice('2009-10-01','2021-09-30'))
# ds_conus = ds[['ACRAINLSM']].sel(time=slice('1986-01-01','2020-12-31'))
# ds_conus

Reading conus404-daily-osn metadata...done


ds_conus.crs

ds_conus.hvplot(x='lon', y='lat', rasterize=True, cmap='viridis', frame_width=600, tiles='OSM', title='Annual average precipitation in mm (2010-2020) PRISM', alpha=0.5)

ds_conus_Pr = ds[['ACRAINLSM']].sel(time=slice('2009-10-01','2021-09-30'))
ds_subset = ds_conus_Pr.resample(time="AS-OCT", label="right").sum()
<!-- # ds_conus.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6) -->

<!-- # ds_subset.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', alpha=0.7, cmap='turbo') -->

In [21]:
%%time
ds_conus_Evap = ds.sel(time=slice('2009-10-01','2010-09-30'))
ds_conus_Trans = ds.sel(time=slice('2009-10-01','2010-09-30'))
ds_conus_Can = ds.sel(time=slice('2009-10-01','2010-09-30'))

ds_subset_Evap = ds_conus_Evap[['ACEDIR']].resample(time="AS-OCT", label="right").sum()
ds_subset_Trans = ds_conus_Trans[['ACETRAN']].resample(time="AS-OCT", label="right").sum()
ds_subset_Can = ds_conus_Can[['ACECAN']].resample(time="AS-OCT", label="right").sum()


# ds_subset_Trans = ds_conus_Trans.resample(time="Y", loffset="Y").sum()

                                          
# Sum the corresponding variables
Evapotranspiration_CONUS404 = ds_subset_Evap['ACEDIR'] +  ds_subset_Trans['ACETRAN'] + ds_subset_Can['ACECAN']

# The result is a DataArray, so if you want to keep it as a Dataset:
Evapotranspiration_CONUS404 = Evapotranspiration_CONUS404.to_dataset(name="AET")

# Now you can inspect the result
Evapotranspiration_CONUS404
# ds_conus.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)

# ds_subset_ET.hvplot.quadmesh(x='lon', y='lat', rasterize=True, 
                             # geo=True, tiles='OSM', alpha=0.7, cmap='turbo')


CPU times: total: 188 ms
Wall time: 185 ms


C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(
C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(
C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(


<xarray.Dataset> Size: 17MB
Dimensions:    (y: 1015, x: 1367, time: 1)
Coordinates:
    lat        (y, x) float32 6MB dask.array<chunksize=(350, 350), meta=np.ndarray>
    lon        (y, x) float32 6MB dask.array<chunksize=(350, 350), meta=np.ndarray>
  * x          (x) float64 11kB -2.732e+06 -2.728e+06 ... 2.728e+06 2.732e+06
  * y          (y) float64 8kB -2.028e+06 -2.024e+06 ... 2.024e+06 2.028e+06
    metpy_crs  object 8B Projection: lambert_conformal_conic
  * time       (time) datetime64[ns] 8B 2010-10-01
Data variables:
    AET        (time, y, x) float32 6MB dask.array<chunksize=(1, 350, 350), meta=np.ndarray>

In [31]:

# Define dataset for full time period
ds_conus_Evap = ds.sel(time=slice('1989-10-01', '2010-09-30'))  # Ensures full water years
ds_conus_Trans = ds.sel(time=slice('1989-10-01', '2010-09-30'))
ds_conus_Can = ds.sel(time=slice('1989-10-01', '2010-09-30'))

# Resample to water years (Oct–Sep)
ds_subset_Evap = ds_conus_Evap[['ACEDIR']].resample(time="AS-OCT", label="right").sum()
ds_subset_Trans = ds_conus_Trans[['ACETRAN']].resample(time="AS-OCT", label="right").sum()
ds_subset_Can = ds_conus_Can[['ACECAN']].resample(time="AS-OCT", label="right").sum()

# Compute Evapotranspiration (AET)
Evapotranspiration_CONUS404 = ds_subset_Evap['ACEDIR'] + ds_subset_Trans['ACETRAN'] + ds_subset_Can['ACECAN']
Evapotranspiration_CONUS404 = Evapotranspiration_CONUS404.to_dataset(name="AET")

# Define output directory
output_dir = "C:/Users/adi10136/OneDrive - Iowa State University/Desktop/ET_WaterYears"
os.makedirs(output_dir, exist_ok=True)


C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(
C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(
C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(


In [36]:
import xarray as xr
import rioxarray as rio
import os

# Define dataset for full time period
ds_conus_Evap = ds.sel(time=slice('1989-10-01', '2010-09-30'))  # Ensures full water years
ds_conus_Trans = ds.sel(time=slice('1989-10-01', '2010-09-30'))
ds_conus_Can = ds.sel(time=slice('1989-10-01', '2010-09-30'))

# Resample to water years (Oct–Sep)
ds_subset_Evap = ds_conus_Evap[['ACEDIR']].resample(time="AS-OCT", label="right").sum()
ds_subset_Trans = ds_conus_Trans[['ACETRAN']].resample(time="AS-OCT", label="right").sum()
ds_subset_Can = ds_conus_Can[['ACECAN']].resample(time="AS-OCT", label="right").sum()

# Compute Evapotranspiration (AET)
Evapotranspiration_CONUS404 = ds_subset_Evap['ACEDIR'] + ds_subset_Trans['ACETRAN'] + ds_subset_Can['ACECAN']
Evapotranspiration_CONUS404 = Evapotranspiration_CONUS404.to_dataset(name="AET")

Evapotranspiration_CONUS404 = Evapotranspiration_CONUS404.rio.write_crs(ds_conus_Evap.crs.metpy.cartopy_crs).drop_vars(['lat', 'lon']).compute()

# **Ensure CRS is set ONCE before looping**
CRS_VALUE = 'EPSG:4326'  # Set CRS (Modify if needed)

# if not hasattr(Evapotranspiration_CONUS404, 'rio') or Evapotranspiration_CONUS404.rio.crs is None:
#     Evapotranspiration_CONUS404 = Evapotranspiration_CONUS404.rio.write_crs(CRS_VALUE.crs.metpy.cartopy_crs).drop_vars(['lat', 'lon']).compute()

# Define output directory
output_dir = "C:/Users/adi10136/OneDrive - Iowa State University/Desktop/ET_WaterYears"
os.makedirs(output_dir, exist_ok=True)

# Loop through each water year from 1990 to 2010
for year in range(1990, 2011):  
    print(f"Processing Water Year {year}...")

    # Select the data for the given water year and compute mean AET
    ds_mean_Annual_ET = Evapotranspiration_CONUS404.sel(time=str(year)).mean(dim="time")

    # Reproject to EPSG:4326
    ds_mean_Annual_ET = ds_mean_Annual_ET.rio.reproject(CRS_VALUE)

    # Define output path and save raster
    output_path = os.path.join(output_dir, f"ET_Mean_Annual_Evapotranspiration_WY{year}.tif")
    ds_mean_Annual_ET.rio.to_raster(output_path)

    print(f"Saved: {output_path}")

print("Processing complete! All water year rasters saved.")


C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(
C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(
C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(


Processing Water Year 1990...
Saved: C:/Users/adi10136/OneDrive - Iowa State University/Desktop/ET_WaterYears\ET_Mean_Annual_Evapotranspiration_WY1990.tif
Processing Water Year 1991...
Saved: C:/Users/adi10136/OneDrive - Iowa State University/Desktop/ET_WaterYears\ET_Mean_Annual_Evapotranspiration_WY1991.tif
Processing Water Year 1992...
Saved: C:/Users/adi10136/OneDrive - Iowa State University/Desktop/ET_WaterYears\ET_Mean_Annual_Evapotranspiration_WY1992.tif
Processing Water Year 1993...
Saved: C:/Users/adi10136/OneDrive - Iowa State University/Desktop/ET_WaterYears\ET_Mean_Annual_Evapotranspiration_WY1993.tif
Processing Water Year 1994...
Saved: C:/Users/adi10136/OneDrive - Iowa State University/Desktop/ET_WaterYears\ET_Mean_Annual_Evapotranspiration_WY1994.tif
Processing Water Year 1995...
Saved: C:/Users/adi10136/OneDrive - Iowa State University/Desktop/ET_WaterYears\ET_Mean_Annual_Evapotranspiration_WY1995.tif
Processing Water Year 1996...
Saved: C:/Users/adi10136/OneDrive - Iowa

In [37]:
import xarray as xr
import rioxarray as rio
import os

# Define dataset for full time period
ds_conus_Evap = ds.sel(time=slice('1989-10-01', '2010-09-30'))  # Ensures full water years
ds_conus_Trans = ds.sel(time=slice('1989-10-01', '2010-09-30'))
ds_conus_Can = ds.sel(time=slice('1989-10-01', '2010-09-30'))

# Resample to water years (Oct–Sep)
ds_subset_Evap = ds_conus_Evap[['ACEDIR']].resample(time="AS-OCT", label="right").sum()
ds_subset_Trans = ds_conus_Trans[['ACETRAN']].resample(time="AS-OCT", label="right").sum()
ds_subset_Can = ds_conus_Can[['ACECAN']].resample(time="AS-OCT", label="right").sum()

# Compute Evapotranspiration (AET)
Evapotranspiration_CONUS404 = ds_subset_Evap['ACEDIR'] + ds_subset_Trans['ACETRAN'] + ds_subset_Can['ACECAN']
Evapotranspiration_CONUS404 = Evapotranspiration_CONUS404.to_dataset(name="AET")

C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(
C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(
C:\Users\adi10136\AppData\Local\anaconda3\envs\CONUS404_test\lib\site-packages\xarray\groupers.py:487: FutureWarning: 'AS-OCT' is deprecated and will be removed in a future version, please use 'YS-OCT' instead.
  self.index_grouper = pd.Grouper(


In [38]:
%%time
ds_mean_Annual_ET = Evapotranspiration_CONUS404.mean(dim='time')
ds_mean_Annual_ET
# ds_mean.hvplot(x='lon', y='y', rasterize=True, cmap='viridis', frame_width=600, tiles='OpenTopoMap', title='Annual average precipitation in mm (1980-2020) CONUS404 - PRISM', alpha=0.5)
# ds_mean_Annual_ET.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', title = 'Mean annual evapotranspiration: 2016 -WY2021', cmap='viridis').opts('Image', alpha=0.6)

CPU times: total: 15.6 ms
Wall time: 4.51 ms


<xarray.Dataset> Size: 17MB
Dimensions:    (y: 1015, x: 1367)
Coordinates:
    lat        (y, x) float32 6MB dask.array<chunksize=(350, 350), meta=np.ndarray>
    lon        (y, x) float32 6MB dask.array<chunksize=(350, 350), meta=np.ndarray>
  * x          (x) float64 11kB -2.732e+06 -2.728e+06 ... 2.728e+06 2.732e+06
  * y          (y) float64 8kB -2.028e+06 -2.024e+06 ... 2.024e+06 2.028e+06
    metpy_crs  object 8B Projection: lambert_conformal_conic
Data variables:
    AET        (y, x) float32 6MB dask.array<chunksize=(350, 350), meta=np.ndarray>

In [39]:
ds_mean_Annual_ET = ds_mean_Annual_ET.rio.write_crs(ds_conus_Evap.crs.metpy.cartopy_crs).drop_vars(['lat', 'lon']).compute()

In [40]:
ds_mean_Annual_ET = ds_mean_Annual_ET.rio.reproject('EPSG:4326')

In [25]:
ds_mean_Annual_ET

<xarray.Dataset> Size: 7MB
Dimensions:      (x: 1884, y: 916)
Coordinates:
  * x            (x) float64 15kB -138.7 -138.7 -138.7 ... -57.12 -57.08 -57.04
  * y            (y) float64 7kB 57.34 57.3 57.25 57.21 ... 17.72 17.68 17.63
    metpy_crs    object 8B Projection: lambert_conformal_conic
    spatial_ref  int32 4B 0
Data variables:
    AET          (y, x) float32 7MB nan nan nan nan nan ... nan nan nan nan nan

ds_mean_Annual_ET = ds_mean_Annual_ET.rio.write_crs("EPSG:4326", inplace=True)

# Verify that the CRS and spatial information is in place
print(ds_mean_Annual_ET.rio.crs)

In [27]:
ds_mean_Annual_ET.hvplot(x='x', y='y', rasterize=True, cmap='viridis', frame_width=600, tiles='OpenTopoMap', title='Annual average precipitation in mm (1980-2020) CONUS404 - PRISM', alpha=0.5)

:DynamicMap   []
   :Overlay
      .Tiles.I :Tiles   [x,y]
      .Image.I :Image   [x_,y_]   (AET)

# Convert AET to a numerical type (e.g., float32)
ds_mean_Annual_ET['AET'] = ds_mean_Annual_ET['AET'].astype('float32')

# Verify the conversion
print(ds_mean_Annual_ET['AET'].dtype

In [26]:
output_path = "ET_Mean_annual_evapotranspiration_WY2010.tif"
ds_mean_Annual_ET.rio.to_raster(output_path)

### OpenET

In [119]:
dataset_OET = ee.ImageCollection('OpenET/ENSEMBLE/CONUS/GRIDMET/MONTHLY/v2_0').filterDate('2016-01-01','2022-01-01')
ds_OET = geemap.ee_to_xarray(dataset_OET, crs="EPSG:4326", scale=0.036)

ds_OET = ds_OET.chunk({'time': 10})
#  print(f"Reading {dataset} metadata...", end='')
ds_OET = ds_OET.metpy.parse_cf()
print("done")
ds_OET = ds_OET.sortby('time')
ds_OET

done


C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\indexing.py:1443: PerformanceWarning: Slicing with an out-of-order index is generating 10 times more chunks
  return self.array[key]
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\indexing.py:1443: PerformanceWarning: Slicing with an out-of-order index is generating 10 times more chunks
  return self.array[key]
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\indexing.py:1443: PerformanceWarning: Slicing with an out-of-order index is generating 10 times more chunks
  return self.array[key]
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\indexing.py:1443: PerformanceWarning: Slicing with an out-of-order index is generating 10 times more chunks
  return self.array[key]
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\indexing.py:1443: PerformanceWarning: Slicing with an out-of-order index is generating 10 times more chunks


<xarray.Dataset>
Dimensions:                (time: 1800, lon: 10000, lat: 5000)
Coordinates:
  * time                   (time) datetime64[ns] 2016-01-01 ... 2021-12-01
  * lon                    (lon) float64 -180.0 -179.9 -179.9 ... 179.9 180.0
  * lat                    (lat) float64 -89.98 -89.95 -89.91 ... 89.95 89.98
    metpy_crs              object Projection: latitude_longitude
Data variables:
    et_ensemble_mad        (time, lon, lat) float32 dask.array<chunksize=(1, 10000, 5000), meta=np.ndarray>
    et_ensemble_mad_min    (time, lon, lat) float32 dask.array<chunksize=(1, 10000, 5000), meta=np.ndarray>
    et_ensemble_mad_max    (time, lon, lat) float32 dask.array<chunksize=(1, 10000, 5000), meta=np.ndarray>
    et_ensemble_mad_count  (time, lon, lat) float32 dask.array<chunksize=(1, 10000, 5000), meta=np.ndarray>
    et_ensemble_mad_index  (time, lon, lat) float32 dask.array<chunksize=(1, 10000, 5000), meta=np.ndarray>
    et_ensemble_sam        (time, lon, lat) float32 dask.array<chunksize=(1, 10000, 5000), meta=np.ndarray>
Attributes:
    max_mirrored_version:  1724191304697896
    crs:                   EPSG:4326

In [120]:
ds_OET_ET = ds_OET[['et_ensemble_mad']].sel(time=slice('2016-01-01', '2022-01-01'))
ds_subset_ET = ds_OET_ET.resample(time="Y").sum()


In [121]:
ds_subset_ET

<xarray.Dataset>
Dimensions:          (time: 6, lon: 10000, lat: 5000)
Coordinates:
  * lon              (lon) float64 -180.0 -179.9 -179.9 ... 179.9 179.9 180.0
  * lat              (lat) float64 -89.98 -89.95 -89.91 ... 89.91 89.95 89.98
    metpy_crs        object Projection: latitude_longitude
  * time             (time) datetime64[ns] 2016-12-31 2017-12-31 ... 2021-12-31
Data variables:
    et_ensemble_mad  (time, lon, lat) float32 dask.array<chunksize=(1, 10000, 5000), meta=np.ndarray>
Attributes:
    max_mirrored_version:  1724191304697896
    crs:                   EPSG:4326

In [122]:
# ds_OET.hvplot(x='lon', y='y', rasterize=True, cmap='viridis', frame_width=600, tiles='OpenTopoMap', title='Actual Evapotranspiration 2016 - 2021', alpha=0.5)

print("CONUS404 time dimension:", ds_conus['time'].values)
print("CONUS404 time dimension:", ds_OET['time'].values)

In [123]:
%%time
ds_OET_ET = ds_OET[['et_ensemble_mad']].sel(time=slice('2016-01-01', '2022-01-01'))
ds_subset_ET = ds_OET_ET.resample(time="Y").sum()
ds_subset_ET

CPU times: total: 93.8 ms
Wall time: 102 ms


<xarray.Dataset>
Dimensions:          (time: 6, lon: 10000, lat: 5000)
Coordinates:
  * lon              (lon) float64 -180.0 -179.9 -179.9 ... 179.9 179.9 180.0
  * lat              (lat) float64 -89.98 -89.95 -89.91 ... 89.91 89.95 89.98
    metpy_crs        object Projection: latitude_longitude
  * time             (time) datetime64[ns] 2016-12-31 2017-12-31 ... 2021-12-31
Data variables:
    et_ensemble_mad  (time, lon, lat) float32 dask.array<chunksize=(1, 10000, 5000), meta=np.ndarray>
Attributes:
    max_mirrored_version:  1724191304697896
    crs:                   EPSG:4326

In [124]:
%%time
ds_mean_Annual_OpenET = ds_subset_ET.mean(dim='time')
ds_mean_Annual_OpenET

CPU times: total: 15.6 ms
Wall time: 3 ms


<xarray.Dataset>
Dimensions:          (lon: 10000, lat: 5000)
Coordinates:
  * lon              (lon) float64 -180.0 -179.9 -179.9 ... 179.9 179.9 180.0
  * lat              (lat) float64 -89.98 -89.95 -89.91 ... 89.91 89.95 89.98
    metpy_crs        object Projection: latitude_longitude
Data variables:
    et_ensemble_mad  (lon, lat) float32 dask.array<chunksize=(10000, 5000), meta=np.ndarray>

In [125]:
ds_mean_Annual_OpenET = ds_mean_Annual_OpenET.rename({'lon': 'x', 'lat': 'y'})
# ds_mean_Annual_OpenET

In [126]:
# If 'AET' is the main variable you're working with
ds_mean_Annual_OpenET = ds_mean_Annual_OpenET.transpose('y', 'x')  # For single band
# ds_mean_Annual_OpenET.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)

In [127]:
# ds_mean_Annual_OpenET = ds_mean_Annual_OpenET.chunk({'y': 350, 'x': 350})
ds_mean_Annual_OpenET.compute()

MemoryError: Unable to allocate 1.86 GiB for an array with shape (10, 10000, 5000) and data type float32

In [ ]:
# ##### Export the raster to GeoTIFF
output_path = "Mean_annual_ET_OpenETV2.tif"
ds_mean_Annual_OpenET.rio.to_raster(output_path)

In [50]:
ds_OET = ds_OET.drop_vars('metpy_crs')
print(ds['time'].values)

['1979-10-01T00:00:00.000000000' '1979-10-02T00:00:00.000000000'
 '1979-10-03T00:00:00.000000000' ... '2022-09-29T00:00:00.000000000'
 '2022-09-30T00:00:00.000000000' '2022-10-01T00:00:00.000000000']


In [ ]:
## lLC spatial reference system
x = 'x'
y = 'y'
print(crs_info.longitude_of_central_meridian)

In [22]:
crs_info = ds_conus.crs
xx = ds_conus.x.values
yy = ds_conus.y.values
globe = ccrs.Globe(ellipse='sphere', semimajor_axis=6370000, semiminor_axis=6370000)
lcc = ccrs.LambertConformal(globe=globe,
                            central_longitude=crs_info.longitude_of_central_meridian, 
                            central_latitude=crs_info.latitude_of_projection_origin,
                            standard_parallels=crs_info.standard_parallel)
print(xx)
print(yy)

[-2732000. -2728000. -2724000. ...  2724000.  2728000.  2732000.]
[-2028000. -2024000. -2020000. ...  2020000.  2024000.  2028000.]


In [23]:
lcc_wkt = lcc.to_wkt()

In [64]:

# Reproject OpenET dataset to Lambert Conformal
source_proj = pyproj.Proj('EPSG:4326')
target_proj = pyproj.Proj(lcc.proj4_init)

# Function to reproject coordinates
def reproject_coordinates(lon, lat, src_proj, tgt_proj):
    transformer = pyproj.Transformer.from_proj(src_proj, tgt_proj, always_xy=True)
    return transformer.transform(lon, lat)

# Extract lat/lon values
lon = ds_OET['lon'].values
lat = ds_OET['lat'].values

# Create meshgrid for lat/lon
lon_mesh, lat_mesh = np.meshgrid(lon, lat)

# Reproject coordinates
lon_reproj, lat_reproj = reproject_coordinates(lon_mesh, lat_mesh, source_proj, target_proj)

# Step 5: Prepare the reprojected PRISM dataset
ds_OET_reproj = ds_OET.assign_coords({'lon_reproj': (('lat', 'lon'), lon_reproj), 'lat_reproj': (('lat', 'lon'), lat_reproj)})

# Interpolate PRISM data to CONUS404 grid
interp_data = {}
for var in ds_OET.data_vars:
    interp_data[var] = ds_OET[var].interp(lon=ds_conus['lon'], lat=ds_conus['lat'],  method='nearest') #  method='nearest'

ds_OET_interp = xr.Dataset(interp_data, coords={'lon': ds_conus['lon'], 'lat': ds_conus['lat'], 'time': ds_OET['time']})
ds_OET_interp

C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chunks(*args)
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chunks(*args)
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chunks(*args)
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chunks(*args)
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chun

<xarray.Dataset>
Dimensions:                (time: 1800, y: 1015, x: 1367)
Coordinates:
  * time                   (time) datetime64[ns] 2016-01-01 ... 2021-12-01
    spatial_ref            int32 0
    lon                    (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>
    lat                    (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>
  * x                      (x) float64 -2.732e+06 -2.728e+06 ... 2.732e+06
  * y                      (y) float64 -2.028e+06 -2.024e+06 ... 2.028e+06
    metpy_crs              object Projection: lambert_conformal_conic
Data variables:
    et_ensemble_mad        (time, y, x) float32 dask.array<chunksize=(1, 350, 350), meta=np.ndarray>
    et_ensemble_mad_min    (time, y, x) float32 dask.array<chunksize=(1, 350, 350), meta=np.ndarray>
    et_ensemble_mad_max    (time, y, x) float32 dask.array<chunksize=(1, 350, 350), meta=np.ndarray>
    et_ensemble_mad_count  (time, y, x) float32 dask.array<chunksize=(1, 350, 350), meta=np.ndarray>
    et_ensemble_mad_index  (time, y, x) float32 dask.array<chunksize=(1, 350, 350), meta=np.ndarray>
    et_ensemble_sam        (time, y, x) float32 dask.array<chunksize=(1, 350, 350), meta=np.ndarray>

In [60]:
%%time
ds_OET_ET = ds_OET_interp[['et_ensemble_mad']].sel(time=slice('2016-01-01', '2022-01-01'))
ds_subset_ET = ds_OET_ET.resample(time="Y").sum()
# ds_conus.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)
# ds_subset_ET.hvplot.quadmesh(x='lon', y='lat', rasterize=True, 
                             # geo=True, tiles='OSM', alpha=0.7, cmap='turbo')

CPU times: total: 688 ms
Wall time: 697 ms


In [61]:
%%time
ds_mean_Annual_OpenET = ds_subset_ET.mean(dim='time')
ds_mean_Annual_OpenET
# ds_mean_Annual_ET.hvplot.quadmesh(x='lon', y='lat', rasterize=True, 
                             # geo=True, tiles='OSM', alpha=0.7, cmap='turbo')

CPU times: total: 0 ns
Wall time: 4.01 ms


<xarray.Dataset>
Dimensions:          (y: 1015, x: 1367)
Coordinates:
    spatial_ref      int32 0
    lon              (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>
    lat              (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>
  * x                (x) float64 -2.732e+06 -2.728e+06 ... 2.728e+06 2.732e+06
  * y                (y) float64 -2.028e+06 -2.024e+06 ... 2.024e+06 2.028e+06
    metpy_crs        object Projection: lambert_conformal_conic
Data variables:
    et_ensemble_mad  (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>

In [62]:
##### Export the raster to GeoTIFF
output_path = "Mean_annual_ET_OpenET.tif"
ds_mean_Annual_OpenET.rio.to_raster(output_path)

In [65]:
# ds_mean_Annual_OpenET['time'] = ds_mean_Annual_OpenET.indexes['time'].normalize()
# ds_mean_Annual_ET['time'] = ds_mean_Annual_ET.indexes['time'].normalize()

In [66]:
# common_times = np.intersect1d(ds_mean_Annual_ET['time'].values, ds_mean_Annual_OpenET['time'].values)
# print("Common time periods:", common_times)

In [67]:
# common_times = np.intersect1d(ds_mean_Annual_ET['time'].values, ds_mean_Annual_OpenET['time'].values)
# ds_conus = ds_conus.sel(time=common_times)
# ds_prism_interp = ds_prism_interp.sel(time=common_times)

In [72]:
# Sum the corresponding variables
Evapotranspiration_BIAS = ds_mean_Annual_OpenET['et_ensemble_mad'] - ds_mean_Annual_ET['AET']
# Diff = ds_mean_Annual_OpenET - ds_mean_Annual_ET
# print(Diff)
# The result is a DataArray, so if you want to keep it as a Dataset:
Evapotranspiration_BIAS = Evapotranspiration_BIAS.to_dataset(name="AET_BIAS")

# Now you can inspect the result
Evapotranspiration_BIAS

<xarray.Dataset>
Dimensions:      (y: 1015, x: 1367)
Coordinates:
    spatial_ref  int32 0
    lon          (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>
    lat          (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>
  * x            (x) float64 -2.732e+06 -2.728e+06 ... 2.728e+06 2.732e+06
  * y            (y) float64 -2.028e+06 -2.024e+06 ... 2.024e+06 2.028e+06
    metpy_crs    object Projection: lambert_conformal_conic
Data variables:
    AET_BIAS     (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>

In [73]:
Evapotranspiration_BIAS.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', title = 'Mean difference CONUS404-PRISM (mm/day)', cmap='viridis').opts('Image', alpha=0.6)

:DynamicMap   []
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [lon,lat]   (AET_BIAS)

In [69]:
##### Export the raster to GeoTIFF
output_path = "Mean_annual_ET_BIAS.tif"
Evapotranspiration_BIAS.rio.to_raster(output_path)

### PRISM

In [27]:
dataset = ee.ImageCollection("OREGONSTATE/PRISM/AN81d").filterDate("2010-01-01", "2020-12-31")
ds = geemap.ee_to_xarray(dataset, crs="EPSG:4326", scale=0.25)

ds = ds.chunk({'time': 10})
#  print(f"Reading {dataset} metadata...", end='')
ds = ds.metpy.parse_cf()
print("done")

ds_prism = ds
ds_prism

done


<xarray.Dataset>
Dimensions:    (time: 4017, lon: 1440, lat: 720)
Coordinates:
  * time       (time) datetime64[ns] 2010-01-01T12:00:00 ... 2020-12-30T12:00:00
  * lon        (lon) float64 -179.9 -179.6 -179.4 -179.1 ... 179.4 179.6 179.9
  * lat        (lat) float64 -89.88 -89.62 -89.38 -89.12 ... 89.38 89.62 89.88
    metpy_crs  object Projection: latitude_longitude
Data variables:
    ppt        (time, lon, lat) float32 dask.array<chunksize=(10, 1440, 720), meta=np.ndarray>
    tmean      (time, lon, lat) float32 dask.array<chunksize=(10, 1440, 720), meta=np.ndarray>
    tmin       (time, lon, lat) float32 dask.array<chunksize=(10, 1440, 720), meta=np.ndarray>
    tmax       (time, lon, lat) float32 dask.array<chunksize=(10, 1440, 720), meta=np.ndarray>
    tdmean     (time, lon, lat) float32 dask.array<chunksize=(10, 1440, 720), meta=np.ndarray>
    vpdmin     (time, lon, lat) float32 dask.array<chunksize=(10, 1440, 720), meta=np.ndarray>
    vpdmax     (time, lon, lat) float32 dask.array<chunksize=(10, 1440, 720), meta=np.ndarray>
Attributes: (12/20)
    date_range:               [347155200000, 1647648000000]
    description:              <p>The PRISM daily and monthly datasets are gri...
    keywords:                 ['climate', 'daily', 'geophysical', 'oregonstat...
    period:                   1
    period_mapping:           [347155200000, 1647648000000]
    product_tags:             ['precipitation', 'climate', 'weather', 'temper...
    ...                       ...
    visualization_0_bands:    ppt
    visualization_0_max:      50.0
    visualization_0_min:      0.0
    visualization_0_name:     Precipitation
    visualization_0_palette:  red,yellow,green,cyan,purple
    crs:                      EPSG:4326

In [36]:
ds_PRISM_Pr = ds_prism[['ppt']].sel(time=slice('2010-01-01','2020-12-31'))
ds_subset_P = ds_PRISM_Pr.resample(time="M", loffset="M").sum()
# ds_conus.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)

ds_subset_P.hvplot.quadmesh(x='lon', y='lat', rasterize=True, 
                             geo=True, tiles='OSM', alpha=0.7, cmap='turbo')

C:\Users\adi10136\AppData\Local\Temp\ipykernel_9636\3554846086.py:2: FutureWarning: Following pandas, the `loffset` parameter to resample will be deprecated in a future version of xarray.  Switch to using time offset arithmetic.
  ds_subset_P = ds_PRISM_Pr.resample(time="M", loffset="M").sum()


:DynamicMap   [time]
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [lon,lat]   (ppt)

ds_prism.hvplot(x='lon', y='lat', rasterize=True, cmap='viridis', frame_width=600, tiles='OSM', title='Annual average precipitation in mm (2010-2020) PRISM', alpha=0.5)

In [9]:
ds_prism = ds_prism.drop_vars('metpy_crs')

In [10]:
# # Rechunk the datasets to have similar chunk sizes
# ds_prism = ds_prism.chunk({'time': 10, 'lat': 100, 'lon': 100})
# ds_conus = ds_conus.chunk({'time': 10, 'y': 100, 'x': 100})

In [11]:
print("CONUS404 time dimension:", ds_conus['time'].values)
print("CONUS404 time dimension:", ds_prism['time'].values)

CONUS404 time dimension: ['1986-01-01T00:00:00.000000000' '1986-01-02T00:00:00.000000000'
 '1986-01-03T00:00:00.000000000' ... '2020-12-29T00:00:00.000000000'
 '2020-12-30T00:00:00.000000000' '2020-12-31T00:00:00.000000000']
CONUS404 time dimension: ['1986-01-01T12:00:00.000000000' '1986-01-02T12:00:00.000000000'
 '1986-01-03T12:00:00.000000000' ... '2020-12-28T12:00:00.000000000'
 '2020-12-29T12:00:00.000000000' '2020-12-30T12:00:00.000000000']


### SPATIAL REFERENCE TO LLC (PRISM)

In [22]:
## lLC spatial reference system
x = 'x'
y = 'y'
print(crs_info.longitude_of_central_meridian)

-97.9000015258789


In [23]:
crs_info = ds_conus.crs
xx = ds_conus.x.values
yy = ds_conus.y.values
globe = ccrs.Globe(ellipse='sphere', semimajor_axis=6370000, semiminor_axis=6370000)
lcc = ccrs.LambertConformal(globe=globe,
                            central_longitude=crs_info.longitude_of_central_meridian, 
                            central_latitude=crs_info.latitude_of_projection_origin,
                            standard_parallels=crs_info.standard_parallel)
print(xx)
print(yy)

[-2732000. -2728000. -2724000. ...  2724000.  2728000.  2732000.]
[-2028000. -2024000. -2020000. ...  2020000.  2024000.  2028000.]


In [24]:
lcc_wkt = lcc.to_wkt()

In [25]:

# Reproject PRISM dataset to Lambert Conformal
source_proj = pyproj.Proj('EPSG:4326')
target_proj = pyproj.Proj(lcc.proj4_init)

# Function to reproject coordinates
def reproject_coordinates(lon, lat, src_proj, tgt_proj):
    transformer = pyproj.Transformer.from_proj(src_proj, tgt_proj, always_xy=True)
    return transformer.transform(lon, lat)

# Extract lat/lon values
lon = ds_prism['lon'].values
lat = ds_prism['lat'].values

# Create meshgrid for lat/lon
lon_mesh, lat_mesh = np.meshgrid(lon, lat)

# Reproject coordinates
lon_reproj, lat_reproj = reproject_coordinates(lon_mesh, lat_mesh, source_proj, target_proj)

# Step 5: Prepare the reprojected PRISM dataset
ds_prism_reproj = ds_prism.assign_coords({'lon_reproj': (('lat', 'lon'), lon_reproj), 'lat_reproj': (('lat', 'lon'), lat_reproj)})

# Interpolate PRISM data to CONUS404 grid
interp_data = {}
for var in ds_prism.data_vars:
    interp_data[var] = ds_prism[var].interp(lon=ds_conus['lon'], lat=ds_conus['lat'], method='nearest')

ds_prism_interp = xr.Dataset(interp_data, coords={'lon': ds_conus['lon'], 'lat': ds_conus['lat'], 'time': ds_prism['time']})


C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chunks(*args)
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chunks(*args)
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chunks(*args)
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chunks(*args)
C:\Users\adi10136\AppData\Local\anaconda3\Lib\site-packages\xarray\core\missing.py:715: PerformanceWarning: Increasing number of chunks by factor of 12
  _, rechunked = chunkmanager.unify_chun

In [26]:
ds_prism_interp
# print(ds_prism_interp.indexes)
# print(ds_conus.indexes)
# print(ds_prism_interp)
print("CONUS404 time dimension:", ds_prism_interp['time'].values)

CONUS404 time dimension: ['1980-12-31T12:00:00.000000000' '1981-01-01T12:00:00.000000000'
 '1981-01-02T12:00:00.000000000' ... '2020-12-28T12:00:00.000000000'
 '2020-12-29T12:00:00.000000000' '2020-12-30T12:00:00.000000000']


ds_prism_interp.hvplot(x='x', y='y', rasterize=True, cmap='viridis', frame_width=600, tiles='OpenTopoMap', title='Annual average precipitation in mm (2010-2020) PRISM', alpha=0.5)

ds_prism_interp.hvplot.quadmesh(x='lon', y='lat', rasterize=True, cmap='viridis', frame_width=600, tiles='OSM', title='Annual average precipitation in mm (2010-2020) PRISM', alpha=0.5)
ds_prism_interp.ppt.sel(time='2019-06-22').hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)

ds_conus.ACRAINLSM.sel(time='2019-06-22').hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)

### Normalize dates

In [27]:
ds_conus['time'] = ds_conus.indexes['time'].normalize()
ds_prism_interp['time'] = ds_prism_interp.indexes['time'].normalize()

### # Resample

In [28]:
# Resample

ds_subset_PRISM = ds_prism_interp.ppt.resample(time="Y").sum()
# ds_subset_PRISM.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', cmap='viridis').opts('Image', alpha=0.6)

In [29]:
ds_subset_CONUS = ds_conus.ACRAINLSM.resample(time="Y").sum()
# ds_subset_CONUS.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', title ='Annual agregation CONUS404', cmap='viridis').opts('Image', alpha=0.6)

In [30]:
print("CONUS404 time dimension:", ds_conus['time'].values)
print("PRISM time dimension:", ds_prism_interp['time'].values)

CONUS404 time dimension: ['1980-01-01T00:00:00.000000000' '1980-01-02T00:00:00.000000000'
 '1980-01-03T00:00:00.000000000' ... '2020-12-29T00:00:00.000000000'
 '2020-12-30T00:00:00.000000000' '2020-12-31T00:00:00.000000000']
PRISM time dimension: ['1980-12-31T00:00:00.000000000' '1981-01-01T00:00:00.000000000'
 '1981-01-02T00:00:00.000000000' ... '2020-12-28T00:00:00.000000000'
 '2020-12-29T00:00:00.000000000' '2020-12-30T00:00:00.000000000']


In [31]:
var_prism = 'ppt'  
var_conus = 'ACRAINLSM'

# Debug: Print time dimensions before alignment
print("CONUS404 time dimension:", ds_conus['time'].values)
print("PRISM time dimension:", ds_prism_interp['time'].values)

common_times = np.intersect1d(ds_conus['time'].values, ds_prism_interp['time'].values)
print("Common time periods:", common_times)


CONUS404 time dimension: ['1980-01-01T00:00:00.000000000' '1980-01-02T00:00:00.000000000'
 '1980-01-03T00:00:00.000000000' ... '2020-12-29T00:00:00.000000000'
 '2020-12-30T00:00:00.000000000' '2020-12-31T00:00:00.000000000']
PRISM time dimension: ['1980-12-31T00:00:00.000000000' '1981-01-01T00:00:00.000000000'
 '1981-01-02T00:00:00.000000000' ... '2020-12-28T00:00:00.000000000'
 '2020-12-29T00:00:00.000000000' '2020-12-30T00:00:00.000000000']
Common time periods: ['1980-12-31T00:00:00.000000000' '1981-01-01T00:00:00.000000000'
 '1981-01-02T00:00:00.000000000' ... '2020-12-28T00:00:00.000000000'
 '2020-12-29T00:00:00.000000000' '2020-12-30T00:00:00.000000000']


In [32]:
common_times = np.intersect1d(ds_conus['time'].values, ds_prism_interp['time'].values)
ds_conus = ds_conus.sel(time=common_times)
ds_prism_interp = ds_prism_interp.sel(time=common_times)

In [33]:
# Check if common times are not empty
if common_times.size == 0:
    raise ValueError("No overlapping time periods found between CONUS404 and PRISM datasets.")

In [34]:
ds_conus = ds_conus.sel(time=common_times)

In [35]:
aligned_conus, aligned_prism = xr.align(ds_conus[var_conus], ds_prism_interp[var_prism], join='inner')

In [36]:
Diff = aligned_conus - aligned_prism
print(Diff)

<xarray.DataArray (time: 14610, y: 1015, x: 1367)>
dask.array<sub, shape=(14610, 1015, 1367), dtype=float32, chunksize=(10, 350, 350), chunktype=numpy.ndarray>
Coordinates:
    lat        (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>
    lon        (y, x) float32 dask.array<chunksize=(350, 350), meta=np.ndarray>
  * time       (time) datetime64[ns] 1980-12-31 1981-01-01 ... 2020-12-30
  * x          (x) float64 -2.732e+06 -2.728e+06 ... 2.728e+06 2.732e+06
  * y          (y) float64 -2.028e+06 -2.024e+06 ... 2.024e+06 2.028e+06
    metpy_crs  object Projection: lambert_conformal_conic


In [37]:
ds = Diff
ds_mean = ds.mean(dim='time')
# ds_mean.hvplot(x='lon', y='y', rasterize=True, cmap='viridis', frame_width=600, tiles='OpenTopoMap', title='Annual average precipitation in mm (1980-2020) CONUS404 - PRISM', alpha=0.5)
ds_mean.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', title = 'Mean difference CONUS404-PRISM (mm/day)', cmap='viridis').opts('Image', alpha=0.6)

:DynamicMap   []
   :Overlay
      .WMTS.I  :WMTS   [Longitude,Latitude]
      .Image.I :Image   [lon,lat]   (value)

In [38]:
###### Export the raster to GeoTIFF
output_path = "Pr_mean_CONUS404-PRISM(1980-2020).tif"
ds_mean.rio.to_raster(output_path)

CPLE_AppDefinedError: Deleting Pr_mean_CONUS404-PRISM(1980-2020).tif.ovr failed: Permission denied

#### Relative differences

R_Diff = (aligned_conus / aligned_prism)
R_Diff = R_Diff.where(aligned_prism != 0)
print(R_Diff)

R_Diff_mean = R_Diff.mean(dim='time')
R_Diff_mean.hvplot.quadmesh(x='lon', y='lat', rasterize=True, geo=True, tiles='OSM', title = 'Relative mean difference CONUS404-PRISM (%)', cmap='viridis').opts('Image', alpha=0.6)
